## IMPLEMENT BRIN AND PAGE’S PAGERANK ALGORITHM

### BASE ALGORITHM TO WEIGHT WEBPAGES

In order to implement the "Base Algorithm to Wight Web Pages", we are going to follow the following steps, for at the end obtain a PySpark DataFrame that will contain each web page with their corresponding weight and ranking, according to "Brin and Page's PageRank Algorithm". 

# Steps to implement **Page Rank Algorithm**
* Check Data Structure and Extract relevant data: [Document ID, List of links]
* Transform *List of links* to *List od Docuemts ID*: *Forward Links Table*
* Calculate *Number of output links*
* Construct *Reverse Links Table* from *Forward Links Table*
* Initialize *Page Rank Table*
* Recalculate *Page Rank Table* until:
  * All the *Page Rank* values are stable
  * Reach number of iterations (sugested value: 20 iterations)

In [ ]:
import pandas as pd
import re
import numpy as np

In [ ]:
from pyspark.sql.types import *
from pyspark.sql.types import ArrayType, StringType,LongType
from pyspark.sql import functions as F

In [ ]:
spark.conf.set("spark.sql.execution.arrow.enabled", "false")

### 1) Check Data Raw Structure and Extract Relevant Data

First we check the DataFrame, and we can see that the relevant columns for constructing a Page Rank DataFrame are the following:

*  **title**: which contains the title/name of the wikipedia document
*  **id**: the id of the wikipedia article
* **text**: contains the content of the article. This column contains the most relevant information for computing the Page Rank, because it contains the links to other Wikipedia documents that are in that article.

In [ ]:
wikipediaDF=spark.read.parquet("dbfs:/databricks-datasets/wikipedia-datasets/data-001/en_wikipedia/articles-only-parquet")

# to test the algorithm we are using 0.002 fraction of the whole database:
PartialWikipediaDF = wikipediaDF.sample(fraction = 0.002, seed = 13).cache()

display(PartialWikipediaDF)

title id revisionId revisionTimestamp revisionUsername revisionUsernameId text Harold Kushner 13992 660927680 2015-05-05T10:45:27.000+0000 KasparBot 24420788 {{Hatnote|For the mathematician see [[Harold J. Kushner]]}} {{Infobox person |name = Harold Samuel Kushner |image = |image_size = |caption = |birth_date = {{Birth year and age|1935}} |birth_place = [[Brooklyn, New York]], [[United States]] |death_date = |death_place = |occupation = Rabbi, author |religion = [[Conservative Judaism]] |notable_works = ''[[When Bad Things Happen to Good People]]'', ''[[When All You've Ever Wanted Isn't Enough]]'' }} Rabbi '''Harold Samuel Kushner''' is a prominent [[United States|American]] [[rabbi]] aligned with the progressive wing of [[Conservative Judaism]],{{Citation needed|date=November 2013}} and a popular author. == Education == Born in [[Brooklyn, New York|Brooklyn]], Kushner was educated at [[Columbia University]] and later obtained his rabbinical ordination from the [[Jewish Theological Seminary of America|Jewish Theological Seminary]] (JTS) in 1960. The same institution awarded him a doctoral degree in Bible in 1972. Kushner has also studied at the [[Hebrew University of Jerusalem]], taught at [[Clark University]] and the Rabbinical School of the JTS, and received six [[honorary doctorates]]. == Congregational Rabbi == He served as the congregational rabbi of Temple Israel of Natick, in [[Natick, Massachusetts]] for 24 years and belongs to the [[Rabbinical Assembly]]. == Author == He is the author of a best selling book on the [[problem of evil]], ''[[When Bad Things Happen to Good People]].'' Written following the death of his son, Aaron, from the premature aging disease [[progeria]], the book deals with questions about human suffering, [[God]], [[omnipotence]] and [[theodicy]]. Aaron was born in 1963 and died in 1977; the book was published in 1981. Kushner has written a number of other popular theological books, such as ''How Good Do We Have to Be?'' (Dedicated to his grandson, Carl), ''To Life!'' and many others. In collaboration with the late [[Chaim Potok]], Kushner co-edited ''Etz Hayim: A Torah Commentary'', the new official [[Torah]] commentary of the [[Conservative Judaism|Conservative movement]], which was jointly published in 2001 by the [[Rabbinical Assembly]] and the [[Jewish Publication Society]]. His ''Living a Life That Matters'' became a best seller in the fall of 2001. Kushner's book, ''The Lord Is My Shepherd'', was a meditation on the [[Psalm 23|Twenty-Third Psalm]] released in 2003. Kushner also wrote a response to Simon Wiesenthal's question of forgiveness in the book ''[[The Sunflower: On the Possibilities and Limits of Forgiveness]].'' == List of publications == * ''[[Conquering Fear: Living Boldly in an Uncertain World]]'' Published in 2009, is a theological piece that addresses fears of terrorism, natural disasters, rejection, growing old and offer suggestions on how best to cope, ultimately living with purpose and differentiating between God and nature. * ''[[Faith & Family: Favorite Sermons of Rabbi Harold S. Kushner]]'' published in October 2007 * ''[[Practice Random Acts of Kindness: Bring More Peace, Love, And Compassion]]'' published in 2007 * ''[[Overcoming Life's Disappointments]]'' published in 2006 * ''[[The Lord Is My Shepherd: Healing Wisdom of the Twenty-third Psalm]]'' published in 2003 * ''[[Who Needs God]]'' published in 1989 * ''[[Living a Life That Matters: Resolving the Conflict Between Conscience and Success]]'' published in 2001 * ''[[How Good Do We Have to Be? A New Understanding of Guilt and Forgiveness]]'' published in 1997 * ''[[When Children ask about God: A Guide for Parents Who Don't Always Have All the Answers]]'' published in 1995 * ''[[To Life: A Celebration of Jewish Being and Thinking]]'' published in 1994 * ''[[When All You've Ever Wanted Isn't Enough|When All You've Ever Wanted Isn't Enough: The Search for a Life That Matters]]'' published in 1986 * ''[[When Bad Things 

To extract the relevant information (links that are contained in each document), we are going to use  a python function that will extract the links in each document. That python function will be defined later as an UDF (user defines function),in order to extend the functions of the framework to be use on multiple DataFrames. 

To do this we need to know how are the links written in the documents. After reviewing several document samples, we can see that there are several formats in which the links are written:

* Enclosed in double brackets: **[[ *name_of_article* ]]**
* Enclosed in double brackets with a | in the middle:
**[[ *name_of_article* | *name_shown_in_article* ]]**. In this case we are only interested in the *name_of_article*, not the *name_shown_in_article*. 
* Category links: **[[Category: *name_of_article*]]**
* Links inside of **{{}}**: some examples are:
  * **{{ see also | *name_of_article* }}**
  * **{{ further | *name_of_article* }}**
  * ** {{ main | *name_of_article* | *name_of_article* | *name_of_article* }}**
    * to generalize, we are going to look only to these particular examples and ignore the rest inside of {{}}
  
And some examples of links that are not exactly links are the following:
* **[[File:name_of_image.jpg...]]** or **[[Image: name_of_image.jpg]]**: in this example we need to look inside of this double brackets, and avoid the file/image name. 
* **[[#Reference-name_of_reference | name_show_in_article]]**: the *name_of_reference* are not exactly articles, but references inside of the document that we are not interested about.

In [ ]:
### User Define Function to extract the links given a single document text/body ###

def parse_links(document_text):
    # lowercase all the letters in the document body string
    document_body = document_text.lower()
    
    # finds all the article names inside of [[]]
    data = re.findall(r'\[\[(.+?)\]\]', document_body)
    
    # finds all the article names inside of {{}}
    data2 = re.findall(r'\{\{(.+?)\}\}', document_body)
    
    if len(data)>0: # if there are links in the article
        
        ### links inside of [[]] ###
        # to fetch the article name when [[name_article | text_in_article]]
        links = [s.split('|')[0].lower() for s in data]
        
        # to avoid the [[]] when [[File:...]]
        links = [s for s in links if 'file' not in s]
        
        # to avoid the [[]] when [[Image:...]]
        links = [s for s in links if 'image:' not in s]
        
        # to obtaine name after a : for example: [[Category: name_article]]
        links = [s.split(':')[1] if "category:" in s else s for s in links]
        
        # to avoid references or internal links inside an article (example: Soccer#Brazil)
        links = [s.split('#')[0] if "#" in s else s for s in links]
        
        # append non-empty article names
        links = [s for s in links if len(s) > 0]
        
    else: # if no links inside of [[]] are found in the article
        links = []
        
    if len(data2) > 0: # if found any links inside of {{}}
    
        ### links inside of {{}} ###
        # to obtain the article in formats {{see also|...}}, {{further|...}} and {{main|...}}
        links2 = [s for s in data2 if "see also" in s[:13] or "further" in s[:13] or "main" in s[:13]]
        
        # to obtain the content after the |
        links2 = [s.split('|')[1:] for s in links2 if "|" in s]
        
        # to flat the list when many articles in see also, further or main
        flatten_list = lambda irregular_list:[element for item in irregular_list for element in flatten_list(item)] if type(irregular_list) is list else [irregular_list]
        links2 = flatten_list(links2)
        
    else: # if no links in {{ found in the article
        links2 = []
    
    # return the two list unified
    return links + links2

# user define function for parsing the links
parse_links_udf = udf(parse_links,ArrayType(StringType()))

# user define function to lowercase the titles of the documents in the "title" column
tolower_udf = udf(lambda x: x.lower())


With the user define function we created above, we create the `parsedDF` DataFrame by mapping the `lower_udf` function to the "title" column to each row, and mapping the `parse_links_udf` function to the "text" column to each row, and also selecting the "id" column. With that we obtain a data frame with only the name of the articles/links that each document contains inside:

In [ ]:
# Parsed DF
parsedDF = PartialWikipediaDF.select(tolower_udf("title").alias("title"), "id", parse_links_udf("text").alias("links"))

display(parsedDF)


title id links harold kushner 13992 List(harold j. kushner, brooklyn, new york, united states, conservative judaism, when bad things happen to good people, when all you've ever wanted isn't enough, united states, rabbi, conservative judaism, brooklyn, new york, columbia university, jewish theological seminary of america, hebrew university of jerusalem, clark university, honorary doctorates, natick, massachusetts, rabbinical assembly, problem of evil, when bad things happen to good people, progeria, god, omnipotence, theodicy, chaim potok, torah, conservative judaism, rabbinical assembly, jewish publication society, psalm 23, the sunflower: on the possibilities and limits of forgiveness, conquering fear: living boldly in an uncertain world, faith & family: favorite sermons of rabbi harold s. kushner, practice random acts of kindness: bring more peace, love, and compassion, overcoming life's disappointments, the lord is my shepherd: healing wisdom of the twenty-third psalm, who needs god, living a life that matters: resolving the conflict between conscience and success, how good do we have to be? a new understanding of guilt and forgiveness, when children ask about god: a guide for parents who don't always have all the answers, to life: a celebration of jewish being and thinking, when all you've ever wanted isn't enough, when bad things happen to good people, the bible, death and state funeral of ronald reagan, washington national cathedral, lifetime achievement award, jewish book council, wikipedia:persondata, brooklyn, new york, united states, 1935 births, living people, 20th-century rabbis, 21st-century rabbis, american conservative rabbis, american jewish theologians, process theologians, jewish american writers, jewish theological seminary of america semikhah recipients, columbia university alumni, hebrew university of jerusalem alumni, people from brooklyn, people from greater boston, erasmus hall high school alumni) july 1 15844 List(ayumi hamasaki, leap year, new year's day, 69, tiberius julius alexander, roman legion, alexandria, allegiance, vespasian, roman emperor, 552, battle of taginae, byzantine empire, narses, ostrogoths, totila, 1097, battle of dorylaeum (1097), crusaders, bohemond i of antioch, seljuk turks, kilij arslan i, 1431, battle of la higueruela, granada, kingdom of castile, reconquista, 1523, johann esch and heinrich voes, lutheran, roman catholic, brussels, 1569, union of lublin, grand duchy of lithuania, real union, polish–lithuanian commonwealth, 1643, westminster assembly, parliament of england, church of england, westminster abbey, 1690, glorious revolution, battle of the boyne, julian calendar, 1766, jean-françois de la barre, pyre, voltaire, dictionnaire philosophique, roman catholic, abbeville, 1770, lexell's comet, 1782, raid on lunenburg, nova scotia (1782), privateer, lunenburg, nova scotia, 1837, civil registration, 1855, quinault treaty, quinault people, quileute people, 1858, charles darwin, alfred russel wallace, evolution, linnean society, 1862, russian state library, princess alice of the united kingdom, louis iv, grand duke of hesse, american civil war, battle of malvern hill, seven days campaign, george b. mcclellan, peninsula campaign, 1863, keti koti, suriname, slavery, battle of gettysburg, 1867, constitution act, 1867, constitution of canada, canadian confederation, federation, dominion, john a. macdonald, prime minister of canada, canada day, 1870, united states department of justice, 1873, prince edward island, canadian confederation, 1874, sholes and glidden typewriter, typewriter, 1878, universal postal union, 1879, charles taze russell, the watchtower, 1881, telephone call, st. stephen, new brunswick, calais, maine, cardwell reforms, childers reforms, british army, 1885, reciprocity (canadian politics), fishery, 1890, bermuda, telegraphy, 1898, spanish–american war, battle of san juan hill, santiago de cuba, 1903, 1903 tour de france, 1908, sos, distress signal, 1911, agadir 

### 2) Create the Forward Links Table

In order to know how many links each document fowards to, we need to create the **Forward Links Table**, wich contains the id of all the links that each document forwards to that are available in the `wikipediDF` dataframe. 

To do that, we are first going to create a Pandas dataframe, that only contains the title of the documents and their corresponding id. We are able to use a Pandas DataFrame because this information is static, and will be used in a distributed way. This pandas DataFrame will be stored in a *broadcast* variable, in order to be used and be accessible by other tasks. 

Later, we create a python function (`text_links_2idx`) to direct title to their correspind "id". In this function we will use the broadcast variable of the `titleidPDF` dataframe, in order to reduce the communication costs when creating the `ForwardDF` pyspark DataFrame.

In [ ]:
# pySpark DataFrame with "id" and "title" of all the articles in the wikipediaDF
titleidDF=wikipediaDF.select("id",tolower_udf("title").alias("title"))

# convert the PySpark DataFrame to a Pandas DataFrame
titleidPDF=titleidDF.toPandas()

broadcast_title_idPDF = sc.broadcast(titleidPDF)

def text_links_2idx(links):
    # take out the dataframe from the broadcast variable
    title_idxPDF = broadcast_title_idPDF.value
    if ( len(links)>0):
    # Look in title column if the elements in the list links exists, and if it exists
    # gets his id value. The result is converted to a list.
        result = title_idxPDF[title_idxPDF.title.isin(links)].id.to_list()
    else:
        result = [] 
    return result

# we create a user define function of the text_links_2idx function
udf_text_links_2idx = udf(text_links_2idx, ArrayType(LongType()))

# Forward Links Table 
ForwardDF = parsedDF.select("id", udf_text_links_2idx("links").alias("links")).cache()



We obtain a pyspark dataframe that shows in an array format, all the ids of all the links that each page/document forwards:

In [ ]:
display(ForwardDF)

id links 13992 List(22776, 26137, 30106, 30343, 6310, 6623, 51273, 67416, 63914, 205224, 274804, 1758494, 2400603, 1847678, 3434750, 5042765, 4116424, 4977543, 116853, 17132030, 27755959, 32177496, 32177496) 15844 List(14533, 14880, 15651, 15786, 16578, 17012, 17062, 863, 881, 1006, 1529, 3079, 3080, 3415, 3464, 3708, 4031, 21255, 21332, 21638, 22428, 22504, 23035, 23071, 23235, 23844, 24095, 24135, 32375, 32570, 32927, 33809, 34039, 34242, 34360, 34415, 34548, 34549, 34551, 34553, 34592, 34595, 34600, 34601, 34602, 34604, 34605, 34606, 34608, 34609, 34612, 34616, 34618, 34622, 34624, 34629, 34630, 34631, 34632, 34635, 34636, 34639, 34648, 34650, 34652, 34655, 34656, 34658, 34659, 34662, 34664, 34668, 34669, 34670, 34672, 34673, 34674, 34677, 34689, 34691, 34703, 34707, 34708, 34715, 34716, 34717, 34719, 34722, 34724, 34745, 34746, 34752, 34754, 34755, 34756, 34759, 34760, 34761, 34768, 34769, 34770, 34772, 34775, 34776, 34785, 34787, 34789, 34790, 34791, 34793, 34813, 34844, 34845, 34846, 34847, 34851, 34864, 34886, 34901, 34903, 34938, 34939, 34966, 34968, 34980, 35020, 35060, 35073, 35075, 35076, 35102, 35220, 35497, 35499, 35502, 35514, 35675, 35709, 35802, 35808, 35821, 35825, 35849, 35852, 35856, 35983, 35984, 36116, 36127, 36163, 36164, 36175, 36225, 36226, 36610, 36741, 36907, 25645, 25994, 26779, 26828, 26908, 26989, 27318, 27358, 27992, 10501, 11775, 12067, 12186, 12441, 12466, 13275, 13404, 13456, 29831, 30010, 31183, 32293, 4849, 4887, 5468, 5573, 5666, 5873, 5955, 7175, 7299, 7411, 17505, 17895, 19127, 19898, 20097, 43226, 43245, 44365, 44474, 46209, 46732, 46945, 47374, 48630, 49107, 49650, 50591, 50767, 51550, 52502, 52563, 52592, 53308, 56638, 57322, 58171, 66730, 67127, 67941, 68318, 69080, 69607, 69886, 73525, 37575, 37754, 38591, 38593, 38605, 38620, 38653, 42477, 60921, 61099, 61103, 61188, 61641, 61865, 62237, 62266, 62811, 192746, 154144, 157674, 159919, 316937, 319684, 325832, 327754, 208639, 209915, 213016, 213219, 161971, 162843, 163531, 164920, 168257, 277783, 75319, 76593, 78172, 79774, 80486, 226146, 228309, 229473, 341286, 341746, 342375, 147456, 147570, 151995, 293645, 294740, 294853, 299482, 307491, 312871, 84577, 85471, 87603, 88160, 88833, 89691, 250974, 251224, 258889, 426402, 241833, 246574, 247079, 398093, 406703, 261243, 261695, 264756, 368549, 370783, 371475, 375969, 380252, 358719, 359360, 362843, 476400, 333714, 337525, 169183, 173061, 174474, 174662, 434974, 439325, 644754, 647641, 382196, 391106, 392258, 410386, 413202, 214884, 216554, 219117, 573330, 576282, 577911, 178766, 180279, 184413, 450329, 456252, 516011, 142806, 145605, 585705, 589713, 599326, 558203, 562864, 562989, 764818, 536709, 541467, 543800, 497050, 731854, 738739, 747099, 750274, 750683, 680893, 854480, 862259, 911202, 482088, 482178, 483214, 487395, 489752, 841474, 1046240, 1046971, 1049954, 1100593, 1100615, 711553, 1060452, 1067941, 1070084, 961559, 962711, 1364993, 1375046, 613879, 614250, 615769, 97078, 1255179, 1265589, 1269740, 984642, 991844, 1182866, 1189231, 1561855, 1566044, 1570753, 1573279, 1162218, 1165289, 1168459, 1170055, 1172850, 1026131, 1587142, 1597706, 1414381, 1414789, 928966, 1282415, 1296423, 1298858, 1689241, 1646211, 1658232, 1659101, 619138, 1007558, 1927763, 1879905, 1887170, 2886260, 1773913, 1734619, 1744167, 1746291, 2230840, 2243467, 771224, 876280, 883369, 886011, 1942253, 1950984, 2164693, 2167549, 2174883, 2175171, 2181342, 2185643, 2297926, 2312049, 1454147, 2270191, 1234962, 1239853, 2534714, 2569864, 3016684, 2002934, 1975834, 1991536, 1500943, 1506324, 2190087, 2079757, 2097193, 2458960, 2472696, 2836372, 2839273, 2850259, 2333459, 2344243, 2600885, 2704190, 2979842, 2387401, 2399263, 2400438, 2417608, 1830414, 1328219, 1338706, 2437436, 2456255, 2039684, 1800624, 1810677, 99878, 100729, 104977, 806370, 810499, 2510772, 3169722, 3186277, 3196403, 2667707, 3137442, 3315152, 3276584, 5175814, 5183633, 3560294, 4291131, 4480933, 3892451, 5010702, 5029935, 5042916, 4452869, 4746542,

### 3) Calculate the Numer of output links in each document

For implementing the Page Rank algorithm we need the number of links each document forwards/outputs to. To do this we are going to use the `size` pyspark function on the `ForwardDF` dataframe, and obtain the length of each links array in the `links` column. 

For using in the PageRank algorithm, we are going to convert it to a Pandas dataframe, because this table is static.

In [ ]:
from pyspark.sql.functions import size
count_linksDF = ForwardDF.select("id", size("links").alias("num_outputs"))

count_linksPDF = count_linksDF.toPandas()

### 4) Create the Reverse Links Table 

For computing the PageRank algorithm, we need the links that are directed to each document. In order to create the this Table, we will use the `ForwardDF` dataframe and python that will reverse the ForwardDF table, by putting as an id the ids in array of the links column, and putting in another column the id that it is coming from. Then we groupBy the ids, and create a dataFrame that will contain an `id` column that refers to a document and a `links` column that contains an array with all the documents that contain as a link the document corresponding to the `id` article.

In [ ]:
# Reverse Table
def reverseId(id,links):
    if (len(links)>0):
        reverse = list(set([ (tgt_id,id) for tgt_id in links]))
    else:
        reverse=[]
    return reverse

ForwardRDD = ForwardDF.rdd

#flatMap the reverseID function, and then groupBy the ids. 
ReverseRDD = (ForwardRDD
            .flatMap(lambda r: reverseId(r.id, r.links))
            .groupByKey()
            .map(lambda r: (r[0], list(r[1]))))

ReverseDF = spark.createDataFrame(ReverseRDD, ["id", "links"])

In [ ]:
display(ReverseDF)

id links 34770 List(15844) 2472696 List(15844) 35502 List(15844) 764818 List(15844) 34648 List(15844) 1338706 List(15844) 27277126 List(15844) 9968010 List(21748) 22936 List(21748, 28395, 203112, 390445, 750947, 666538, 1042963, 1566114, 1416893, 626831, 1862386, 771961, 1511309, 2144022, 2158710, 3241426, 2943418, 2370764, 3435522, 5577885, 6806259, 5815621, 5815688, 8580557, 8697315, 9815974, 8541170, 14135875, 10850283, 10852341, 9883318, 6266029, 12428286, 14074061, 18522900, 18522904, 30877959, 15105213, 15114419, 21206827, 21262216, 15129198, 26259456, 21459990, 21460263, 21521730, 21522993, 30269951, 21406900, 21119971, 14928820, 14930378, 14933159, 27921873, 25757480, 37989618, 22060011, 20988621, 20989680, 20990456, 20990608, 21001562, 21003579, 21015330, 21016581, 21032395, 41302404, 18473162, 21823315, 21839937, 20974306, 44277995, 38971385, 44253196, 35920111, 18891725, 21560259, 21560579, 21561241, 21561245, 21561747, 21562103, 24918856, 12282578, 21732898, 21760498, 19955133, 19955715, 19956022, 26638197, 19804226, 19829723, 19831502, 19832728, 19857788, 19858031, 29263089, 18625152, 18665846, 18665953, 18667427, 44744525, 39668230, 45630665, 21363383, 21363640, 41688252, 19899240, 19899864, 19900709, 19901169, 19901349, 19915812, 19915835, 22000448, 18994714, 26111740, 21886374, 21934445, 47584785, 21666279, 21666533, 21667308, 21670291, 21731818, 21732555, 41923095, 33572362, 29067512, 33917362, 33951602, 39773533, 47132172, 46278887, 30524825, 41490547, 47625436, 43175680, 30332955, 45206852, 19685000, 46323963, 43341805, 31378438, 15028118, 35324034, 46857697) 38224674 List(21748) 3723196 List(24148) 27779400 List(32838) 70760 List(36517, 1848511, 41001302, 23452007) 30510248 List(36517) 1999824 List(28395) 21632918 List(11407) 65758 List(29782, 434089, 145325, 2945074, 3440224, 5735181, 15195498, 34937573) 48068 List(29782, 394771, 18775035, 21989206) 1814384 List(4545) 44491326 List(4545) 5734 List(5946) 589626 List(6881) 33306 List(19191, 3021954, 5022746, 5925110, 7445713, 14044158, 27905137, 14334411) 357826 List(43460, 13649645) 34526 List(43460) 30873076 List(43460) 4565728 List(43460) 3245566 List(45979) 20618 List(53078) 20374 List(68140, 592949, 97112, 99602, 10940823) 198616 List(73460) 38674 List(38694) 20155864 List(39132) 52826 List(60528) 709064 List(203464) 15069928 List(327536) 15982 List(206453) 7310484 List(206453) 27757074 List(163562) 16230148 List(163562) 276208 List(276208) 168726 List(74095) 526430 List(74095, 1357298) 854 List(80756, 337367, 751851, 714277, 137473, 41298252, 31360383, 13694892) 3797250 List(80756) 29036 List(80765, 5064532) 2621292 List(340510) 65880 List(149681, 619802, 2070246, 7143212, 6458990, 6461310, 23921956) 6333142 List(149681) 422608 List(290145) 2502830 List(290610, 108583, 29164348) 26840 List(293583, 695443, 948631, 964003, 2142287, 30865316, 3658209, 6123320, 10839550, 10604577, 31586506, 19248613, 21063547, 44943846, 37861815) 9609574 List(293583) 47489232 List(306392, 3199391, 3313884, 4723245, 3635758, 17572103, 20851085, 25912824, 27908531, 17689000, 17689361, 37317915, 21995342, 47391482, 34749665, 45397067) 3369762 List(306392, 35010326) 2120482 List(313959, 18147509, 37065707, 39739279) 2257854 List(313959) 25742 List(82738, 1090006, 41861310) 18910 List(82738, 1890199, 2153241) 1394948 List(85672) 518256 List(89074) 4702368 List(256599) 8418 List(420086, 3178607, 3815307, 5663964, 9495122, 30888332, 24033777, 27775353, 21739772, 33865591) 6466 List(432529, 752996, 1791503, 4848945, 30865316, 4044917, 5636280, 9495122, 10376872, 8187015, 10547573, 20548614, 27465678, 26700667, 16691136, 39666305, 42708287, 30323140, 46657777, 12204892, 34854074, 41553542) 9764026 List(432529) 1726422 List(243459) 6738426 List(403902) 56120 List(259541, 260510, 260589, 42531188, 23574353, 42002781, 14536255) 42458074 List(261462) 42606060 List(261727) 11309644 List(261727) 336476 List(369696) 13180026 List(369696) 23088744 List(364375) 2158058 List(365573) 41968 Li

To improve the Page Rank calculation, we are going to add an extra column, that contains and array with the number of output links that each page in the links column contains. Which means that this extra column will contain an array of the same length as the array in the links column. 

To do this we are going to use the `count_linksPDF` pandas dataframe and a python function that will look in the `count_linksPDF` the number of outputs for each id in the "links" column.

In [ ]:
# broadcast the count_linksPDF variable to be able to use it in the lambda mapping inside of the ReverseDF dataframe. 
broadcast_output_number = sc.broadcast(count_linksPDF)

def links_to_num_outputs(links, count_links):
    result = count_links[count_links.id.isin(links)].num_outputs.to_list()
    
    return result

# convert the links_to_num_outputs function to a user define function variable
udf_links_2_num_outputs = udf(lambda l: links_to_num_outputs(l, count_linksPDF), ArrayType(LongType()))

# map the function to each row to create the new column
ReverseDF = ReverseDF.select("Id", "links", udf_links_2_num_outputs("links").alias("num_outputs_links")).cache()

In [ ]:
display(ReverseDF)

Id links num_outputs_links 34770 List(15844) List(733) 2472696 List(15844) List(733) 35502 List(15844) List(733) 764818 List(15844) List(733) 34648 List(15844) List(733) 1338706 List(15844) List(733) 27277126 List(15844) List(733) 9968010 List(21748) List(138) 22936 List(21748, 28395, 203112, 390445, 750947, 666538, 1042963, 1566114, 1416893, 626831, 1862386, 771961, 1511309, 2144022, 2158710, 3241426, 2943418, 2370764, 3435522, 5577885, 6806259, 5815621, 5815688, 8580557, 8697315, 9815974, 8541170, 14135875, 10850283, 10852341, 9883318, 6266029, 12428286, 14074061, 18522900, 18522904, 30877959, 15105213, 15114419, 21206827, 21262216, 15129198, 26259456, 21459990, 21460263, 21521730, 21522993, 30269951, 21406900, 21119971, 14928820, 14930378, 14933159, 27921873, 25757480, 37989618, 22060011, 20988621, 20989680, 20990456, 20990608, 21001562, 21003579, 21015330, 21016581, 21032395, 41302404, 18473162, 21823315, 21839937, 20974306, 44277995, 38971385, 44253196, 35920111, 18891725, 21560259, 21560579, 21561241, 21561245, 21561747, 21562103, 24918856, 12282578, 21732898, 21760498, 19955133, 19955715, 19956022, 26638197, 19804226, 19829723, 19831502, 19832728, 19857788, 19858031, 29263089, 18625152, 18665846, 18665953, 18667427, 44744525, 39668230, 45630665, 21363383, 21363640, 41688252, 19899240, 19899864, 19900709, 19901169, 19901349, 19915812, 19915835, 22000448, 18994714, 26111740, 21886374, 21934445, 47584785, 21666279, 21666533, 21667308, 21670291, 21731818, 21732555, 41923095, 33572362, 29067512, 33917362, 33951602, 39773533, 47132172, 46278887, 30524825, 41490547, 47625436, 43175680, 30332955, 45206852, 19685000, 46323963, 43341805, 31378438, 15028118, 35324034, 46857697) List(138, 134, 71, 36, 169, 35, 23, 49, 4, 30, 10, 27, 62, 29, 22, 179, 14, 9, 87, 19, 27, 5, 3, 4, 935, 46, 14, 5, 50, 8, 8, 10, 56, 5, 11, 11, 19, 28, 49, 9, 8, 35, 6, 7, 8, 9, 8, 32, 6, 9, 16, 30, 27, 28, 9, 83, 27, 7, 7, 9, 9, 9, 10, 9, 9, 8, 24, 8, 8, 11, 8, 22, 9, 15, 39, 47, 11, 12, 10, 10, 10, 10, 6, 8, 9, 55, 7, 8, 9, 7, 9, 8, 8, 9, 9, 8, 7, 9, 9, 9, 7, 18, 22, 14, 8, 6, 19, 9, 9, 7, 8, 8, 8, 7, 11, 16, 40, 11, 11, 3, 8, 9, 11, 11, 10, 8, 11, 3, 59, 12, 15, 15, 46, 23, 5, 8, 6, 19, 12, 9, 8, 36, 10, 6, 25, 13, 18) 38224674 List(21748) List(138) 3723196 List(24148) List(55) 27779400 List(32838) List(25) 70760 List(36517, 1848511, 41001302, 23452007) List(340, 36, 96, 30) 30510248 List(36517) List(340) 1999824 List(28395) List(134) 21632918 List(11407) List(115) 65758 List(29782, 434089, 145325, 2945074, 3440224, 5735181, 15195498, 34937573) List(191, 64, 181, 36, 94, 26, 12, 5) 48068 List(29782, 394771, 18775035, 21989206) List(191, 28, 76, 48) 1814384 List(4545) List(227) 44491326 List(4545) List(227) 5734 List(5946) List(55) 589626 List(6881) List(71) 33306 List(19191, 3021954, 5022746, 5925110, 7445713, 14044158, 27905137, 14334411) List(28, 17, 4, 53, 41, 9, 6, 10) 357826 List(43460, 13649645) List(520, 52) 34526 List(43460) List(520) 30873076 List(43460) List(520) 4565728 List(43460) List(520) 3245566 List(45979) List(125) 20618 List(53078) List(133) 20374 List(68140, 592949, 97112, 99602, 10940823) List(218, 85, 42, 52, 2) 198616 List(73460) List(235) 38674 List(38694) List(151) 20155864 List(39132) List(55) 52826 List(60528) List(235) 709064 List(203464) List(68) 15069928 List(327536) List(47) 15982 List(206453) List(118) 7310484 List(206453) List(118) 27757074 List(163562) List(476) 16230148 List(163562) List(476) 276208 List(276208) List(15) 168726 List(74095) List(88) 526430 List(74095, 1357298) List(88, 29) 854 List(80756, 337367, 751851, 714277, 137473, 41298252, 31360383, 13694892) List(151, 286, 56, 40, 69, 14, 9, 9) 3797250 List(80756) List(151) 29036 List(80765, 5064532) List(45, 26) 2621292 List(340510) List(62) 65880 List(149681, 619802, 2070246, 7143212, 6458990, 6461310, 23921956) List(276, 100, 16, 48, 13, 21, 41) 6333142 List(149681) List(276) 422608 List(290145) List(145) 2502830 List(290610, 108583, 29164348) List(20, 113, 33

### 5) Create the PageRank dataframe

Before computing the PageRank with the algorithm, we need to initialize the PageRank dataframe, which will contain the an id column with the id of the article and a "Rank" column which will contain the page rank calculation number. 

But first, we need to intialize the algorithm with a Rank number equal to: \\(\frac{0.85}{N}\\), where N is the number of pages in the `ReverseDF` dataframe, and 0.85 is to include a damping factor to the Page Rank algorithm. The `PageRankDF` dataframe will contain the same document ids as in the `ReverseDF` dataframe. 

Also, this new `PageRankDF` pyspark DataFrame will be converted to a Pandas DataFrame to be used in the algorithm.

In [ ]:
# count the number of links/documents in the ReverseDF 
N = ReverseDF.count()
# broadcast this variable to be used in the algorithm
broadcast_N = sc.broadcast(N)


from pyspark.sql.functions import lit
PageRankDF = ReverseDF.withColumn("Rank", lit(0.85/N))
PageRankDF = PageRankDF.select("Id", "Rank")

PageRankPDF = PageRankDF.toPandas()

In [ ]:
display(PageRankDF)

Id Rank 34770 6.490878406756622E-6 2472696 6.490878406756622E-6 35502 6.490878406756622E-6 764818 6.490878406756622E-6 34648 6.490878406756622E-6 1338706 6.490878406756622E-6 27277126 6.490878406756622E-6 9968010 6.490878406756622E-6 22936 6.490878406756622E-6 38224674 6.490878406756622E-6 3723196 6.490878406756622E-6 27779400 6.490878406756622E-6 70760 6.490878406756622E-6 30510248 6.490878406756622E-6 1999824 6.490878406756622E-6 21632918 6.490878406756622E-6 65758 6.490878406756622E-6 48068 6.490878406756622E-6 1814384 6.490878406756622E-6 44491326 6.490878406756622E-6 5734 6.490878406756622E-6 589626 6.490878406756622E-6 33306 6.490878406756622E-6 357826 6.490878406756622E-6 34526 6.490878406756622E-6 30873076 6.490878406756622E-6 4565728 6.490878406756622E-6 3245566 6.490878406756622E-6 20618 6.490878406756622E-6 20374 6.490878406756622E-6 198616 6.490878406756622E-6 38674 6.490878406756622E-6 20155864 6.490878406756622E-6 52826 6.490878406756622E-6 709064 6.490878406756622E-6 15069928 6.490878406756622E-6 15982 6.490878406756622E-6 7310484 6.490878406756622E-6 27757074 6.490878406756622E-6 16230148 6.490878406756622E-6 276208 6.490878406756622E-6 168726 6.490878406756622E-6 526430 6.490878406756622E-6 854 6.490878406756622E-6 3797250 6.490878406756622E-6 29036 6.490878406756622E-6 2621292 6.490878406756622E-6 65880 6.490878406756622E-6 6333142 6.490878406756622E-6 422608 6.490878406756622E-6 2502830 6.490878406756622E-6 26840 6.490878406756622E-6 9609574 6.490878406756622E-6 47489232 6.490878406756622E-6 3369762 6.490878406756622E-6 2120482 6.490878406756622E-6 2257854 6.490878406756622E-6 25742 6.490878406756622E-6 18910 6.490878406756622E-6 1394948 6.490878406756622E-6 518256 6.490878406756622E-6 4702368 6.490878406756622E-6 8418 6.490878406756622E-6 6466 6.490878406756622E-6 9764026 6.490878406756622E-6 1726422 6.490878406756622E-6 6738426 6.490878406756622E-6 56120 6.490878406756622E-6 42458074 6.490878406756622E-6 42606060 6.490878406756622E-6 11309644 6.490878406756622E-6 336476 6.490878406756622E-6 13180026 6.490878406756622E-6 23088744 6.490878406756622E-6 2158058 6.490878406756622E-6 41968 6.490878406756622E-6 36140792 6.490878406756622E-6 10410626 6.490878406756622E-6 2045818 6.490878406756622E-6 381006 6.490878406756622E-6 83448 6.490878406756622E-6 18933424 6.490878406756622E-6 462624 6.490878406756622E-6 15434464 6.490878406756622E-6 168848 6.490878406756622E-6 339526 6.490878406756622E-6 645624 6.490878406756622E-6 2664236 6.490878406756622E-6 38048506 6.490878406756622E-6 19544888 6.490878406756622E-6 390766 6.490878406756622E-6 47946 6.490878406756622E-6 27694 6.490878406756622E-6 31672420 6.490878406756622E-6 9644100 6.490878406756622E-6 450302 6.490878406756622E-6 654286 6.490878406756622E-6 23170240 6.490878406756622E-6 925736 6.490878406756622E-6 846558 6.490878406756622E-6 42090 6.490878406756622E-6 14396 6.490878406756622E-6 1240130 6.490878406756622E-6 20217474 6.490878406756622E-6 1392874 6.490878406756622E-6 152256 6.490878406756622E-6 1636020 6.490878406756622E-6 185196 6.490878406756622E-6 1735206 6.490878406756622E-6 315858 6.490878406756622E-6 28426 6.490878406756622E-6 46762112 6.490878406756622E-6 9516 6.490878406756622E-6 3274114 6.490878406756622E-6 48312 6.490878406756622E-6 713212 6.490878406756622E-6 34056056 6.490878406756622E-6 227164 6.490878406756622E-6 348920 6.490878406756622E-6 42736966 6.490878406756622E-6 25246070 6.490878406756622E-6 23983492 6.490878406756622E-6 8540 6.490878406756622E-6 7930 6.490878406756622E-6 2134024 6.490878406756622E-6 78446 6.490878406756622E-6 353068 6.490878406756622E-6 6877384 6.490878406756622E-6 1686528 6.490878406756622E-6 9783058 6.490878406756622E-6 1691042 6.490878406756622E-6 218746 6.490878406756622E-6 41988252 6.490878406756622E-6 1209386 6.490878406756622E-6 171166 6.490878406756622E-6 44751308 6.490878406756622E-6 3206282 6.490878406756622E-6 4926360 6.490878406756622E-6 8587092 6.490878406756622E-6 6826022 6.490878406756622E-6 1322968 6

## PageRank Algorithm 

The PageRank algorithm can be computed iteratively, in which in each iteration, in each page link:

* The Page Rank of a page A is calculated taking into account the following formula:
  $$PR(A) = \frac{1-d}{N} + d(\sum_{p_j-directed-to-A} \frac{PR(p_j)}{C(p_j)})$$
  
  * where \\(PR(p_j)\\) corresponds to the PageRank of \\(p_j\\), \\(C(p_j)\\) corresponds to the number of links that page \\(p_j\\) have outputs to, and \\(d\\) is the damping factor, which is equal to \\(d=0.85\\)
  
This is repeated iteratively until the Page Rank values are stable or it reaches the maximum number of iterations. 

This steps of the algorithm are computed in the `new_pagerank` python function, that receives the old `PageRankDF`, a list of links (the links that are directing to that row page), and another list containing the number of outputs for each corresponfing link in the list of links (that are going to be for obtaining the \\(C(p_j)\\) value)

In order to implement this algorithm, we are going to make use of the mapping of user defined functions in pyspark dataframes (`new_pagerank` function). So, we defined a *while* loop, that will stop whenever the maximum number of iterations are reached or the norm of the PageRank values doesn't change (to measure the stability of the values). 

Then inside this loop, a PageRank will be calculated from the `ReverseDF` dataframe, where the udf function of `new_pagerank` will be mapped for computing the PageRank of each page (mapping for each row). Then the norm difference between the new Page rank (`NewPageRankPDF`) and the old page rank (`PageRankPDF`), in order to measure the stability of the values. 

This steps are repeted iteratively until one of the conditions is satisfied. At the end, the algorithm returns a DataFrame that is later ordered by the PageRanks values, and assign a Rank Number in order to visualize the more important pages according to the algorithm

In [ ]:
def new_pagerank(list_links, num_outputs, PageRankPdf):
    iter_sum = 0.85/broadcast_N.value
    for i in range(len(list_links)):
        page = list_links[i]
        N = PageRankPdf[PageRankPdf.Id == int(page)].Rank.to_list()
        if len(N) == 0:
            N = 0
        else:
            N = N[0]
        C = num_outputs[i]
        iter_sum += 0.15*(N/C)
    return iter_sum

In [ ]:
from numpy.linalg import norm

norm_rank_diff = norm(PageRankPDF.Rank) # to test the stability
count = 0 # to test the number of iterations

while count < 20 and norm_rank_diff > 1e-30: # checks the conditions
    
    # creates a new udf function with an updated PageRankPDF
    udf_new_pagerank = udf(lambda l, outs: new_pagerank(l, outs, PageRankPDF), FloatType()) 
    
    # calculates the new page rank for each page using the ReverseDF dataframe
    NewPageRankDF = ReverseDF.select("Id", udf_new_pagerank("links", "num_outputs_links").alias("Rank"))
    
    # converts it to a Pandas DataFrame
    NewPageRankPDF = NewPageRankDF.toPandas()
    
    # calculates the norm of the difference of the old and new PageRankPDF
    norm_rank_diff = np.absolute(norm(PageRankPDF.Rank) - norm(NewPageRankPDF.Rank))
    
    #updates the dataframe
    PageRankPDF = NewPageRankPDF
    count += 1

# converts the PageRankPDF pandas dataframe to a pyspark DataFrame
ResultPageRankDF = spark.createDataFrame(PageRankPDF)

from pyspark.sql import Window
import pyspark.sql.functions as psf
from pyspark.sql.functions import dense_rank

wRank = Window.orderBy(psf.desc("Rank"))

# Orders and ranks the values of the pageranks calculated by the algorithm
PageRankOrderDF = ResultPageRankDF.withColumn("PageRank", psf.dense_rank().over(wRank))

In [ ]:
display(PageRankOrderDF)

Id Rank PageRank 3434750 7.947004633024335E-6 1 10568 7.5981029112881515E-6 2 5843419 7.5708426265919115E-6 3 5222 7.514462140534306E-6 4 5042916 7.157873369578738E-6 5 11039790 7.137351985875284E-6 6 14653 7.120738700905349E-6 7 31717 7.1096424107963685E-6 8 19828134 7.107546480256133E-6 9 32927 7.10348740540212E-6 10 25391 7.050826752674766E-6 11 17867 7.05074671714101E-6 12 17675 7.0307455644069705E-6 13 45576306 7.017149073362816E-6 14 15277122 7.017149073362816E-6 14 13369801 7.017149073362816E-6 14 14532 7.006760824879166E-6 15 14533 6.995463536441093E-6 16 31750 6.979324552958133E-6 17 271601 6.978529654588783E-6 18 13834135 6.978529654588783E-6 18 36507935 6.977694283705205E-6 19 22989 6.935465989954537E-6 20 9316 6.9266552600311115E-6 21 448160 6.913944616826484E-6 22 5405 6.909450803505024E-6 23 1165622 6.896558261360042E-6 24 1049844 6.896558261360042E-6 24 410219 6.883596597617725E-6 25 38523 6.883596597617725E-6 25 90516 6.883596597617725E-6 25 96642 6.88051613906282E-6 26 645042 6.876992301840801E-6 27 15573 6.860715075163171E-6 28 18618239 6.853831109765451E-6 29 11867 6.852307706139982E-6 30 3966054 6.846493306511547E-6 31 23565893 6.832501640019473E-6 32 19653842 6.832501640019473E-6 32 43460969 6.832501640019473E-6 32 13166062 6.832501640019473E-6 32 31643578 6.832501640019473E-6 32 38641753 6.832501640019473E-6 32 3383 6.830959137005266E-6 33 57070 6.826102890045149E-6 34 23235 6.819923783041304E-6 35 6889 6.819594091211911E-6 36 8210131 6.81560732118669E-6 37 128608 6.80575294609298E-6 38 23893 6.800473329349188E-6 39 19728 6.7958112595079E-6 40 86224 6.79361573929782E-6 41 26667 6.7871701503463555E-6 42 32070 6.786575340811396E-6 43 3921 6.781110641895793E-6 44 7954681 6.777468570362544E-6 45 19599929 6.7630221565195825E-6 46 5713946 6.753395609848667E-6 47 5650783 6.751672572136158E-6 48 2774053 6.750195097993128E-6 49 497340 6.748427495040232E-6 50 144425 6.7463038249115925E-6 51 24653719 6.745926839357708E-6 52 3343 6.74076727591455E-6 53 5043544 6.739040600223234E-6 54 297809 6.738368938385975E-6 55 2414941 6.7349769778957125E-6 56 4004673 6.734591352142161E-6 57 25148342 6.734591352142161E-6 57 13814694 6.734286216669716E-6 58 77251 6.734286216669716E-6 58 780950 6.734286216669716E-6 58 4025696 6.734286216669716E-6 58 26809 6.734286216669716E-6 58 5058739 6.730700079060625E-6 59 737 6.7294859036337584E-6 60 898 6.727010713802883E-6 61 24624 6.726852006977424E-6 62 22199 6.721665158693213E-6 63 3454 6.72162241244223E-6 64 5407 6.721561931044562E-6 65 4913064 6.716432835673913E-6 66 32597 6.714891696901759E-6 67 29773 6.713138191116741E-6 68 32374 6.710048182867467E-6 69 4764461 6.709553872497054E-6 70 8087628 6.7078690335620195E-6 71 11424 6.7077326093567535E-6 72 10656945 6.707585725962417E-6 73 38493 6.706545264023589E-6 74 26994 6.6995739871344995E-6 75 8569916 6.698033303109696E-6 76 5489 6.697263870591996E-6 77 1051555 6.696815489704022E-6 78 2783508 6.695950105495285E-6 79 1631617 6.695950105495285E-6 79 3462 6.694373951177113E-6 80 33376919 6.6916272771777585E-6 81 859412 6.6916272771777585E-6 81 2185867 6.691188445984153E-6 82 400064 6.690567261102842E-6 83 238674 6.690567261102842E-6 83 312241 6.690567261102842E-6 83 2924002 6.689134352200199E-6 84 17730 6.688084795314353E-6 85 43432956 6.688084795314353E-6 85 22219 6.6869488364318386E-6 86 36464127 6.686253982479684E-6 87 16108700 6.686253982479684E-6 87 4568114 6.686253982479684E-6 87 46980 6.685906100756256E-6 88 6768840 6.685906100756256E-6 88 33241129 6.6857674028142355E-6 89 14000652 6.6857674028142355E-6 89 12789 6.6857674028142355E-6 89 5422296 6.685604603262618E-6 90 129971 6.685604603262618E-6 90 673987 6.685604603262618E-6 90 494894 6.685604603262618E-6 90 185396 6.685604603262618E-6 90 2476315 6.685604603262618E-6 90 16083953 6.685604603262618E-6 90 1156034 6.685604603262618E-6 90 3630320 6.685604603262618E-6 90 3141115 6.685604603262618E-6 90 26866338 6.685604603262618E-6 90 12567453 6.685604603262618E-6 90 18993927 6.685604603262

In [ ]:
# iterations it takes for it to converge
count

Out[48]: 4

In [ ]:
def id_to_title(idx):
    title_idxPDF = broadcast_title_idPDF.value
    return title_idxPDF[title_idxPDF.id == idx]["title"].to_numpy()[0]

udf_id_2_title = udf(id_to_title, StringType())


PageRankResultDF = PageRankOrderDF.select(udf_id_2_title("Id").alias("Title"), "Id","PageRank", "Rank")

display(PageRankResultDF)

Title Id PageRank Rank united states 3434750 1 7.947004633024335E-6 association football 10568 2 7.5981029112881515E-6 france 5843419 3 7.5708426265919115E-6 colombia 5222 4 7.514462140534306E-6 canada 5042916 5 7.157873369578738E-6 animal 11039790 6 7.137351985875284E-6 iran 14653 7 7.120738700905349E-6 united kingdom 31717 8 7.1096424107963685E-6 plant 19828134 9 7.107546480256133E-6 world war ii 32927 10 7.10348740540212E-6 russia 25391 11 7.050826752674766E-6 london 17867 12 7.05074671714101E-6 lithuania 17675 13 7.0307455644069705E-6 2014 in mexican television 45576306 14 7.017149073362816E-6 food vessel 15277122 14 7.017149073362816E-6 food vessel 13369801 14 7.017149073362816E-6 italy 14532 15 7.006760824879166E-6 india 14533 16 6.995463536441093E-6 ukraine 31750 17 6.979324552958133E-6 mangaka 271601 18 6.978529654588783E-6 moyasimon: tales of agriculture 13834135 18 6.978529654588783E-6 shooting at the 2012 summer olympics – men's 10 metre air pistol 36507935 19 6.977694283705205E-6 paris 22989 20 6.935465989954537E-6 england 9316 21 6.9266552600311115E-6 provinces of iran 448160 22 6.913944616826484E-6 china 5405 23 6.909450803505024E-6 serie d 1165622 24 6.896558261360042E-6 football in italy 1049844 24 6.896558261360042E-6 communes of france 410219 25 6.883596597617725E-6 departments of france 38523 25 6.883596597617725E-6 ariège (department) 90516 25 6.883596597617725E-6 communes of the ariège department 96642 26 6.88051613906282E-6 new york city 645042 27 6.876992301840801E-6 japan 15573 28 6.860715075163171E-6 u.s. state 18618239 29 6.853831109765451E-6 germany 11867 30 6.852307706139982E-6 mexico 3966054 31 6.846493306511547E-6 christian congregation in the united states 23565893 32 6.832501640019473E-6 organism 19653842 32 6.832501640019473E-6 christian congregation 43460969 32 6.832501640019473E-6 wagon master 13166062 32 6.832501640019473E-6 cryozoa 31643578 32 6.832501640019473E-6 wagon master 38641753 32 6.832501640019473E-6 brazil 3383 33 6.830959137005266E-6 united states census bureau 57070 34 6.826102890045149E-6 pakistan 23235 35 6.819923783041304E-6 census 6889 36 6.819594091211911E-6 new york 8210131 37 6.81560732118669E-6 population density 128608 38 6.80575294609298E-6 per capita income 23893 39 6.800473329349188E-6 marriage 19728 40 6.7958112595079E-6 1928 summer olympics 86224 41 6.79361573929782E-6 spain 26667 42 6.7871701503463555E-6 republican party (united states) 32070 43 6.786575340811396E-6 basketball 3921 44 6.781110641895793E-6 montreal 7954681 45 6.777468570362544E-6 republic of the congo 19599929 46 6.7630221565195825E-6 fc tyumen 5713946 47 6.753395609848667E-6 iran standard time 5650783 48 6.751672572136158E-6 eudicots 2774053 49 6.750195097993128E-6 single-player video game 497340 50 6.748427495040232E-6 category 144425 51 6.7463038249115925E-6 alpine skiing at the 2010 winter olympics – men's slalom 24653719 52 6.745926839357708E-6 belgium 3343 53 6.74076727591455E-6 democratic party (united states) 5043544 54 6.739040600223234E-6 socialist federal republic of yugoslavia 297809 55 6.738368938385975E-6 russian football national league 2414941 56 6.7349769778957125E-6 lithuania at the 2006 winter olympics 4004673 57 6.734591352142161E-6 lithuania at the 2010 winter olympics 25148342 57 6.734591352142161E-6 armand apell 13814694 58 6.734286216669716E-6 real-time strategy 77251 58 6.734286216669716E-6 warcraft 780950 58 6.734286216669716E-6 chieri 4025696 58 6.734286216669716E-6 starcraft 26809 58 6.734286216669716E-6 sweden 5058739 59 6.730700079060625E-6 afghanistan 737 60 6.7294859036337584E-6 antimony 898 61 6.727010713802883E-6 pop music 24624 62 6.726852006977424E-6 ohio 22199 63 6.721665158693213E-6 bangladesh 3454 64 6.72162241244223E-6 california 5407 65 6.721561931044562E-6 new zealand 4913064 66 6.716432835673913E-6 vilnius 32597 67 6.714891696901759E-6 tennis 29773 68 6.713138191116741E-6 venezuela 32374 69 6.710048182867467E-6 world war i 4764461 70 6.709553872497054E-6 e

# Results Analysis

We can see that we were able to obtain a DataFrame containing the weights of a sample of pages if the `wikipediDF` DataFrame. As we read the first rows of the DataFrame, we can see that the results are coherent. It makes sense that the "United States", "Association Football", "France", "Colombia" and "Canada" are one of the most important pages. 

Additionally, we can see that there are some ties in the `PageRank` column of the DataFrame. This could be related to the fact that we are only using a 0.002 fraction of the whole `wikipediDF` DataFrame or due to the fact that there are pages that do not forward to any page, so the other pages that do contain pages with forwards are contributed a higher weight. 

Also, we can see that with this sample, the weights converge after 4 iterations (`count = 4`). This value may be higher if our sample was bigger. It could be tested when a better cluster is used.

# Conclusion

We can see that with the use of *Brin and Page's Page Rank Algorithm* we are able to compute a pyspark DataFrame that weights each wikipedia web page and ranks each page according to their importance (according to the PageRank Algorithm). We are able to compute this weights by making use of pyspark *lambda* functions, *udf* functions mapped to pyspark dataframes and the use of pandas dataframes. 

In order to compute and test the algorithm, we only took a sample/fraction of 0.002 of the whole Wikipedia Dataframe, because we had only available a cluster with onlyt two cores. With a better cluster (with more cores), a bigger DataFrame can be computed with more pages with a better performance. 

One of the advantages of computing this type of computations in PySpark and not in Pandas, is that Pandas run their computations and operations in a single machine, while on the contrary, PySpark runs on multiple machines. And in this case where we are working with a large dataset (more than 5 million rows), PySpark is more optimal because it processes computations a lot faster than Pandas operations. Other advantage of PySpark is that we can run processes parallely on a distributed cluster, which contains multiple nodes or sometimes a single node. This advantage is good for computing a large amount of data in a much faster way. 

Additionally, because of PySpark's distributed nature in DataFrames and in-memory computation, the processing engine of PySpark allows the process to be efficient and distributed, which makes it reliable, scalable and flexible. Because of these characteristics, the result `PageRankResultDF` DataFrame had no computation or any damage in the data, and was succesfully computed.